# Preparing questions
## File that gets documents relative to each question

In [1]:
K_Passages = 5
PATH_KNOWLEDGE_TRAIN_BASE = 'MSMARCO_biomedical_PT/train.csv'
PATH_KNOWLEDGE_DEV_BASE = 'MSMARCO_biomedical_PT/dev.csv'
PATH_KNOWLEDGE_TEST_BASE = 'MSMARCO_biomedical_PT/test.csv'

PATH_QUESTIONS_SAVE = 'MSMARCO_biomedical_100_pt_true/'

INDEX_KNOWLEDGE_BASE = ["biomedical_100_pt_true"]



## Starting Elastic Search server

In [2]:
#! wget https://artifacts.elastic.co/downloads/elasticsearch/elasticsearch-7.9.2-linux-x86_64.tar.gz -q
#! tar -xzf elasticsearch-7.9.2-linux-x86_64.tar.gz
#! chown -R daemon:daemon elasticsearch-7.9.2
##! chmod 755 -R elasticsearch-7.9.2/bin/elasticsearch
import os
from subprocess import Popen, PIPE, STDOUT
es_server = Popen(['elastic_docs/elasticsearch-7.9.2/bin/elasticsearch'],
                   stdout=PIPE, stderr=STDOUT,
                   preexec_fn=lambda: os.setuid(1)  # as daemon
                  )
# wait until ES has started
! sleep 30

## Preparing Documents

In [3]:
from haystack.document_store.elasticsearch import ElasticsearchDocumentStore
document_store = ElasticsearchDocumentStore(host="localhost", username="", password="")

10/17/2021 20:58:08 - INFO - farm.modeling.prediction_head -   Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .
10/17/2021 20:58:09 - INFO - faiss.loader -   Loading faiss with AVX2 support.
10/17/2021 20:58:09 - INFO - faiss.loader -   Loading faiss.
10/17/2021 20:58:09 - INFO - elasticsearch -   HEAD http://localhost:9200/ [status:200 request:0.005s]
10/17/2021 20:58:09 - INFO - elasticsearch -   HEAD http://localhost:9200/document [status:200 request:0.001s]
10/17/2021 20:58:09 - INFO - elasticsearch -   GET http://localhost:9200/document [status:200 request:0.001s]
10/17/2021 20:58:09 - INFO - elasticsearch -   PUT http://localhost:9200/document/_mapping [status:200 request:0.012s]
10/17/2021 20:58:09 - INFO - elasticsearch -   HEAD http://localhost:9200/label [status:200 request:0.001s]


In [4]:
from haystack.retriever.sparse import ElasticsearchRetriever
retriever = ElasticsearchRetriever(document_store=document_store)

In [5]:
from haystack.pipeline import Pipeline

extractive_pipeline = Pipeline()
extractive_pipeline.add_node(component=retriever, name="ESRetriever1", inputs=["Query"])

In [6]:
res = extractive_pipeline.run(query="O que é transtorno obsessivo compulsivo ?", top_k_retriever=K_Passages, index = INDEX_KNOWLEDGE_BASE)#, index = "teste")
print(res)

10/17/2021 20:58:09 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.007s]


{'query': 'O que é transtorno obsessivo compulsivo ?', 'documents': [{'text': 'Definição médica de transtorno obsessivo-compulsivo. Transtorno obsessivo-compulsivo: um distúrbio psiquiátrico caracterizado por pensamentos obsessivos e ações compulsivas, como limpeza, verificação, contagem ou acumulação. Transtorno obsessivo-compulsivo (OCD), um dos transtornos de ansiedade, é uma condição potencialmente incapacitante que pode persistir ao longo da vida de uma pessoa.', 'score': 29.975657, 'probability': 0.97695422009465, 'question': None, 'meta': {'question': 'Definição do distúrbio do OCD', 'type': 'train', '_split_id': 0}, 'embedding': None, 'id': 'ab9f6d6364f6a88944af5ff551830dc3'}, {'text': 'O transtorno obsessivo-compulsivo (OCD) se enquadra em uma categoria de condições chamadas distúrbios obsessivos-compulsivos e relacionados que incluem: 1 Transtorno Obsessivo-Compulsivo (TOC). 2 Transtorno Dismórfico Corporal. 3 desordem de acumulação.', 'score': 29.738388, 'probability': 0.976

## Reading dataset and getting documents to each question
### Training dataset

In [7]:
import pandas as pd


# Loading the MSMARCO Dataset
qas_train = pd.read_csv(PATH_KNOWLEDGE_TRAIN_BASE, index_col=0).values.tolist()
qas_dev = pd.read_csv(PATH_KNOWLEDGE_DEV_BASE, index_col=0).values.tolist()
qas_test = pd.read_csv(PATH_KNOWLEDGE_TEST_BASE, index_col=0).values.tolist()

In [8]:
train_docs = [] 
for i in range(len(qas_train)):
    res = extractive_pipeline.run(query=qas_train[i][4], top_k_retriever=K_Passages, index = INDEX_KNOWLEDGE_BASE)
    train_docs.append({"question":qas_train[i][4], "answer": qas_train[i][5], "documents":res["documents"]})
    if i %100 == 0:
        print(i)

10/17/2021 20:58:09 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.005s]
10/17/2021 20:58:09 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:58:09 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:58:09 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:58:09 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.003s]
10/17/2021 20:58:09 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.004s]
10/17/2021 20:58:09 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.003s]
10/17/2021 20:58:09 - INFO - elasticsearch -   POST http://localhost:

0


10/17/2021 20:58:09 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.005s]
10/17/2021 20:58:09 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:58:09 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.005s]
10/17/2021 20:58:09 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.003s]
10/17/2021 20:58:09 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.001s]
10/17/2021 20:58:09 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.004s]
10/17/2021 20:58:09 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.004s]
10/17/2021 20:58:09 - INFO - elasticsearch -   POST http://localhost:

10/17/2021 20:58:10 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.005s]
10/17/2021 20:58:10 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.004s]
10/17/2021 20:58:10 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.004s]
10/17/2021 20:58:10 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.006s]
10/17/2021 20:58:10 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.004s]
10/17/2021 20:58:10 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:58:10 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.004s]
10/17/2021 20:58:10 - INFO - elasticsearch -   POST http://localhost:

100


...

10/17/2021 20:59:32 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.006s]
10/17/2021 20:59:32 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:32 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:32 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.006s]
10/17/2021 20:59:32 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:32 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:32 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.004s]
10/17/2021 20:59:32 - INFO - elasticsearch -   POST http://localhost:

22000


10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.004s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.001s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:

10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.001s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.003s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.004s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.001s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:

22100


### Test dataset

In [9]:
test_docs = [] 
for i in range(len(qas_test)):
    res = extractive_pipeline.run(query=qas_test[i][4], top_k_retriever=5, index = INDEX_KNOWLEDGE_BASE)
    test_docs.append({"question":qas_test[i][4], "answer": qas_test[i][5], "documents":res["documents"]})
    if i %100 == 0:
        print(i)

10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.003s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.004s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.007s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.003s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.004s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.001s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:

0


10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.003s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.003s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.005s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.001s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:

10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.003s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.003s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.004s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.003s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.004s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:

10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.003s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.003s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.001s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.003s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.004s]
10/17/2021 20:59:33 - INFO - elasticsearch -   POST http://localhost:

...

10/17/2021 20:59:49 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.007s]
10/17/2021 20:59:49 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:49 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.004s]
10/17/2021 20:59:49 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.003s]
10/17/2021 20:59:49 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:49 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:49 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.001s]
10/17/2021 20:59:49 - INFO - elasticsearch -   POST http://localhost:

4600


10/17/2021 20:59:49 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.006s]
10/17/2021 20:59:49 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:49 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.004s]
10/17/2021 20:59:49 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:49 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.004s]
10/17/2021 20:59:49 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:49 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.003s]
10/17/2021 20:59:49 - INFO - elasticsearch -   POST http://localhost:

10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.004s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.003s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.006s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.005s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.004s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:

4700


### Validation Dataset

In [10]:
eval_docs = [] 
for i in range(len(qas_dev)):
    res = extractive_pipeline.run(query=qas_dev[i][4], top_k_retriever=K_Passages, index = INDEX_KNOWLEDGE_BASE)
    eval_docs.append({"question":qas_dev[i][4], "answer": qas_dev[i][5], "documents":res["documents"]})
    if i %100 == 0:
        print(i)

10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.004s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.003s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.004s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.003s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.004s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.003s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:

0


10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.003s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.001s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:

10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.001s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.003s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.003s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.004s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:

10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.005s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.003s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.001s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.003s]
10/17/2021 20:59:50 - INFO - elasticsearch -   POST http://localhost:

...

10/17/2021 21:00:02 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 21:00:02 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.001s]
10/17/2021 21:00:02 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.004s]
10/17/2021 21:00:02 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.001s]
10/17/2021 21:00:03 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.001s]
10/17/2021 21:00:03 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.004s]
10/17/2021 21:00:03 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.002s]
10/17/2021 21:00:03 - INFO - elasticsearch -   POST http://localhost:

4600


10/17/2021 21:00:03 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.001s]
10/17/2021 21:00:03 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.003s]
10/17/2021 21:00:03 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.001s]
10/17/2021 21:00:03 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.001s]
10/17/2021 21:00:03 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.004s]
10/17/2021 21:00:03 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.001s]
10/17/2021 21:00:03 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.001s]
10/17/2021 21:00:03 - INFO - elasticsearch -   POST http://localhost:

10/17/2021 21:00:03 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.001s]
10/17/2021 21:00:03 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.001s]
10/17/2021 21:00:03 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.001s]
10/17/2021 21:00:03 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.003s]
10/17/2021 21:00:03 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.003s]
10/17/2021 21:00:03 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.001s]
10/17/2021 21:00:03 - INFO - elasticsearch -   POST http://localhost:9200/biomedical_100_pt_true/_search [status:200 request:0.001s]
10/17/2021 21:00:03 - INFO - elasticsearch -   POST http://localhost:

4700


## Preparing tokens for T5

In [11]:
import pandas as pd
import ast

def preprocess(docs):
    questions = []
    answer = []
    for instance in docs:
        question = "question: " + instance["question"]
        documents = ""
        for i in range (K_Passages):
            if i < len(instance["documents"]):
                document_dict = ast.literal_eval(str(instance["documents"][i]))
                documents += document_dict["text"] + " "
        question += " [SEP] context: "+documents
        questions.append(question)
        answer.append(instance["answer"])

    pd_dataset = pd.DataFrame({'question': questions, 'answer' : answer})
    pd_dataset.head()
    
    return(pd_dataset)

pd_dataset_train = preprocess(train_docs)

pd_dataset_val = preprocess(eval_docs)

pd_dataset_test = preprocess(test_docs)



## Saving results

In [12]:
pd_dataset_train.to_csv(PATH_QUESTIONS_SAVE + "train.csv")
pd_dataset_val.to_csv(PATH_QUESTIONS_SAVE + "val.csv")
pd_dataset_test.to_csv(PATH_QUESTIONS_SAVE + "test.csv")



In [13]:
pd.set_option("display.max_colwidth", None)
pd_dataset_test.head(1)

question  \
0  question: implante dentário de custo médio [SEP] context: Implantes de dente único custo. O custo do implante dentário único é geralmente na faixa de US $ 850 a US $ 3500 - este é o preço se tudo correr suavemente. No entanto, se procedimentos adicionais precisam ser feitos, espere pagar até US $ 10.000. No preço médio dos Estados Unidos para um único implante dentário é de cerca de US $ 2.500. Custo médio de implantes dentários em PA. O custo médio de um implante dentário e coroa de um dentista tops US $ 3000. (Pennsylvania dentista cobrando US $ 900 para a coroa); As taxas de implantes são muito altas. Custo médio de implantes dentários em PA. Implantes dentários geralmente custam US $ 1892 na Filadélfia, mas você pode economizar 20%. O que os implantes dentários all-on-4 custam? O custo de um único implante dentário, nos EUA, médias entre US $ 1-3000 por implante, de acordo com o guia de custo do implante dentário.Tn-on-4 implantes dentários requerem quatro implantes para proteger o arco inferior e quatro implantes para o topo Arch.hat fazer todos os implantes dentários de todos os dentários? O custo de um único implante dentário, no U.S., médias entre US $ 1-3000 por implante, de acordo com o Guia de Custo do Implante Dental. Há muita variação em taxas odontológicas, mas o total médio para implante odontológico e coroa associada relatados por dentistas nesta pesquisa foi de cerca de US $ 3.200 - que é US $ 1.800 para o custo do implante dentário, US $ 1.400 para a Coroa - além de outros US $ 600 para um costume abutment. A melhor maneira de determinar o custo real do seu implante dentário, é entrar em contato conosco para uma consulta gratuita. De acordo com DentalimplantCostGuide.com, o implante dentário completo, no U.S., custa cerca de US $ 4250.    

       answer  
0  US $ 4250.